<a href="https://colab.research.google.com/github/atstuyuki/mediapipe/blob/main/mediapipe_shoulder_toCSV_20221213.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# セットアップ

さまざまなカメラアングルから肩の外転角度を算出　訓練用のCSVを作成する

In [ ]:
#google driveのマウント
'''from google.colab import drive
drive.mount('/content/drive')'''

"from google.colab import drive\ndrive.mount('/content/drive')"

#誤検出が多かったので、min_detection_confidence　0.8に変更

In [2]:
# ライブラリーのインストール
!pip install numpy==1.19.3
!pip install mediapipe
# 初期設定 holistic とPoseを用意する　検出感度は0.5＞＞変更可能
import mediapipe as mp
import cv2
mp_holistic = mp.solutions.holistic
mp_pose = mp.solutions.pose
# Initialize MediaPipe Holistic.
holistic = mp_holistic.Holistic(
    static_image_mode=True, min_detection_confidence=0.9)
pose= mp_pose.Pose(
    static_image_mode=True, min_detection_confidence=0.9)
# Prepare DrawingSpec for drawing the face landmarks later.
mp_drawing = mp.solutions.drawing_utils 
drawing_spec = mp_drawing.DrawingSpec(color=[225,0,200],thickness=2, circle_radius=1) #color=[B,G,R]で指定,線の太さと〇の色も指定可能

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


正解の肩外転角度を入力 スライダーバーで10度刻みに指定

In [3]:
true_angle = 90 #@param {type:"slider", min:0, max:180, step:10}


カメラの設置角度指定

In [5]:
cam_angle= 30  #@param {type:"slider", min:-60, max:60, step:15}

右手か左手を指定(is_right Yes=1, NO=0)

In [6]:
is_right_hand=1  #@param ["0", "1"] {allow-input: true}

保存ファイル名を指定

In [7]:
movie_name= "kusu2"#@param {type:"string"}

In [8]:
#手元の動画をgoogle colabにupload

from google.colab import files
import os
uploaded = files.upload()
#uploadedは辞書型なのでファイル名を取り出し、絶対パスを取得してfullpathという変数を当てる
for k in uploaded.keys():
  print('file name:',k)
fullpath=os.path.abspath(k)
print('fullpath:',fullpath)

Saving Movie_09_(A30-90).mp4 to Movie_09_(A30-90).mp4
file name: Movie_09_(A30-90).mp4
fullpath: /content/Movie_09_(A30-90).mp4


In [9]:
cap = cv2.VideoCapture(fullpath) #動画の読み込み
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH)) #幅
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT)) #高
frame_rate = int(cap.get(cv2.CAP_PROP_FPS)) #FPS
fourcc = cv2.VideoWriter_fourcc('m','p','4','v') #mp4出力
out = cv2.VideoWriter('out.mp4', fourcc, frame_rate, (width, height))
print('width:',width)
print('height:',height)
print('frame rate:',frame_rate)

#3次元座標の角度計算の定義
def calculate_3D_angle(a,b,c):
    a = np.array(a) # First
    b = np.array(b) # Mid
    c = np.array(c) # End
    #0がx座標　１がｙ座標　２がｚ座標
    #ベクトルを定義 長さと内積からコサインを計算
    vec_a=a-b
    vec_c=c-b
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_c=np.linalg.norm(vec_c)
    inner_product=np.inner(vec_a, vec_c)
    cos=inner_product/(len_vec_a*len_vec_c)
    
    #角度（ラジアン）の計算
    rad=np.arccos(cos)
    
    #ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#2次元からの角度計算の定義
def calculate_2D_angle(a,b,c):
  a=np.array(a)#firtst
  b=np.array(b)#second
  c=np.array(c)#third
  #[x,y,z]座標から[x,y]のみスライスしてベクトルを作成
  vec_a=a[0:2]-b[0:2]
  vec_c=c[0:2]-b[0:2]
  len_vec_a=np.linalg.norm(vec_a)
  len_vec_c=np.linalg.norm(vec_c)
  inner_product=np.inner(vec_a, vec_c)
  cos=inner_product/(len_vec_a*len_vec_c)
    
#角度（ラジアン）の計算
  rad=np.arccos(cos)
#ラジアンから度数へ変換
  angle=np.rad2deg(rad)
        
  return angle


width: 1080
height: 1920
frame rate: 30


各種測定関数の定義

In [10]:
#体軸からの肩の外転角度測定
#3次元座標の角度計算の定義
def calculate_3D_shoulder_angle(a,b,c,d,e):
    a = np.array(a) # 右肘
    b = np.array(b) # 右肩
    c = np.array(c) # 左肩
    #c1=[b[0], c[1],b[2]]#右肩のx, 左肩のy、右肩のzを取得
    d = np.array(d) # 右股
    e = np.array(e) # 左股
    #0がx座標　１がｙ座標　２がｚ座標
    #中点を定義
    global shoulder_mid
    shoulder_mid = (b+c)/2 #肩の中心座標
    global hip_mid
    hip_mid = (d+e)/2 #股関節の中心座標　world系では0になるはず
    #ベクトルを定義 長さと内積からコサインを計算
    vec_a=hip_mid-shoulder_mid #体軸のベクトル
    vec_b=a-b
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_b=np.linalg.norm(vec_b)
    inner_product=np.inner(vec_a, vec_b)
    cos=inner_product/(len_vec_a*len_vec_b)
    
    #角度（ラジアン）の計算
    rad=np.arccos(cos)
    
    #ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#2次元からの角度計算の定義
def calculate_2D_shoulder_angle(a,b,c,d,e):
    a = np.array(a) # 右肘
    b = np.array(b) # 右肩
    c = np.array(c) # 左肩
    #c1=[b[0], c[1],b[2]]#右肩のx, 左肩のy、右肩のzを取得
    d = np.array(d) # 右股
    e = np.array(e) # 左股
    #0がx座標　１がｙ座標　２がｚ座標
    #中点を定義
    shoulder_mid = (b+c)/2 #肩の中心座標
    hip_mid = (d+e)/2 #股関節の中心座標　world系では0になるはず
  #[x,y,z]座標から[x,y]のみスライスしてベクトルを作成
    vec_a=hip_mid[0:2]-shoulder_mid[0:2]#体軸のベクトル
    vec_b=a[0:2]-b[0:2]
    len_vec_a=np.linalg.norm(vec_a)
    len_vec_b=np.linalg.norm(vec_b)
    inner_product=np.inner(vec_a, vec_b)
    cos=inner_product/(len_vec_a*len_vec_b)
    
#角度（ラジアン）の計算
    rad=np.arccos(cos)
#ラジアンから度数へ変換
    angle=np.rad2deg(rad)
        
    return angle

#面積　sizeの計算 2Dの3点から外積を算出　
def calc_size(a, b, c):
    a=np.array(a[0:2])#先端の座標1(x,yのみ)
    b=np.array(b[0:2])#先端の座標2
    c=np.array(c[0:2])#基部の座標

    vec1=a-c
    vec2=b-c
    
    size=np.cross(vec1,vec2)*10#数字が小さいので10倍しておく
    size=np.abs(size)#絶対値をとる
    return size


#pointの距離計測の関数 a-b（2点間の座標）間の距離を基準となる距離(c-dの距離）で除したものとする
def point_distance(a,b,c,d):
    a=np.array(a)#遠位関節の座標
    b=np.array(b)#近位関節の座標
    c=np.array(c)#基準関節の座標1
    d=np.array(d)#基準関節の座標2
    
    dist1=np.linalg.norm(a-b)
    dist2=np.linalg.norm(c-d)
    distance=dist1/dist2
    return distance 

# サンプルビデオの読み込み＋静止画に分解

In [11]:
# video2images
import os
import shutil
import cv2

# 既にimagesフォルダーがあれば削除
if os.path.isdir('images'):
    shutil.rmtree('images')

os.makedirs('images', exist_ok=True)
 
def video_2_images(video_file= fullpath,   
                   image_dir='./images/', 
                   image_file='%s.png'):
 
    # Initial setting
    i = 0
    interval = 1#適宜調整
    length = 3500
    
    cap = cv2.VideoCapture(video_file)
    while(cap.isOpened()):
        flag, frame = cap.read()  
        if flag == False:  
                break
        if i == length*interval:
                break
        if i % interval == 0:    
           cv2.imwrite(image_dir+image_file % str(int(i/interval)).zfill(6), frame)
        i += 1 
    cap.release()  
 
def main():
    video_2_images()
    
if __name__ == '__main__':
    main()

In [12]:
#pose_landmarkのリストを取得して配列に変換

import numpy as np
landmarklist=[]#空の配列を作成
for index in range(len(mp_holistic.PoseLandmark)):
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_x')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_y')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_z')
    landmarklist.append(mp_holistic.PoseLandmark(index).name+'_visibility')
#リストをarrayに変換
landmarklist=np.array(landmarklist).reshape(1,-1)
#landmarkshape の内容の確認
print('landmark list data type:',landmarklist.dtype)
print('landmark list:',landmarklist)
print('landmark list shape:',landmarklist.shape)


landmark list data type: <U27
landmark list: [['NOSE_x' 'NOSE_y' 'NOSE_z' 'NOSE_visibility' 'LEFT_EYE_INNER_x'
  'LEFT_EYE_INNER_y' 'LEFT_EYE_INNER_z' 'LEFT_EYE_INNER_visibility'
  'LEFT_EYE_x' 'LEFT_EYE_y' 'LEFT_EYE_z' 'LEFT_EYE_visibility'
  'LEFT_EYE_OUTER_x' 'LEFT_EYE_OUTER_y' 'LEFT_EYE_OUTER_z'
  'LEFT_EYE_OUTER_visibility' 'RIGHT_EYE_INNER_x' 'RIGHT_EYE_INNER_y'
  'RIGHT_EYE_INNER_z' 'RIGHT_EYE_INNER_visibility' 'RIGHT_EYE_x'
  'RIGHT_EYE_y' 'RIGHT_EYE_z' 'RIGHT_EYE_visibility' 'RIGHT_EYE_OUTER_x'
  'RIGHT_EYE_OUTER_y' 'RIGHT_EYE_OUTER_z' 'RIGHT_EYE_OUTER_visibility'
  'LEFT_EAR_x' 'LEFT_EAR_y' 'LEFT_EAR_z' 'LEFT_EAR_visibility'
  'RIGHT_EAR_x' 'RIGHT_EAR_y' 'RIGHT_EAR_z' 'RIGHT_EAR_visibility'
  'MOUTH_LEFT_x' 'MOUTH_LEFT_y' 'MOUTH_LEFT_z' 'MOUTH_LEFT_visibility'
  'MOUTH_RIGHT_x' 'MOUTH_RIGHT_y' 'MOUTH_RIGHT_z'
  'MOUTH_RIGHT_visibility' 'LEFT_SHOULDER_x' 'LEFT_SHOULDER_y'
  'LEFT_SHOULDER_z' 'LEFT_SHOULDER_visibility' 'RIGHT_SHOULDER_x'
  'RIGHT_SHOULDER_y' 'RIGHT_SHOULDER_z' 

# MediaPipeで静止画を処理

In [13]:
import cv2
from google.colab.patches import cv2_imshow
import numpy as np
import glob
import time
#変数の初期化
rtshoulderAnglelist=[]
rtshoulderAbductionlist=[]
rtshoulder_3DAnglelist=[]
rtshoulder_3DAbductionlist=[]

ltshoulderAnglelist=[]
ltshoulderAbductionlist=[]
ltshoulder_3DAnglelist=[]
ltshoulder_3DAbductionlist=[]

true_angle_list=[]
cam_angle_list=[]
is_right_hand_list=[]
timelist=[]

#各関節の3次元座標もリスト化する

"""
nose_x_list=[]
nose_y_list=[]
nose_z_list=[]
rtelbow_x_list=[]
rtelbow_y_list=[]
rtelbow_z_list=[]
rtshoulder_x_list=[]
rtshoulder_y_list=[]
rtshoulder_z_list=[]

ltelbow_x_list=[]
ltelbow_y_list=[]
ltelbow_z_list=[]
ltshoulder_x_list=[]
ltshoulder_y_list=[]
ltshoulder_z_list=[]

rthip_x_list=[]
rthip_y_list=[]
rthip_z_list=[]
lthip_x_list=[]
lthip_y_list=[]
lthip_z_list=[]
"""
#肘股関節距離/体軸長
rtelbowhip_distlist=[]
ltelbowhip_distlist=[]
#上腕の長さを体幹の長さで割ったものを変数とする
rtarm_distlist=[]
ltarm_distlist=[]
#股関節幅と体幹軸の長さの比
rthip_distlist=[]
lthip_distlist=[]
#肩幅と体幹軸の長さの比
rtshoulder_distlist=[]
ltshoulder_distlist=[]

data_land = np.zeros((0,132))

# image file names to files in list format
files=[]
for name in sorted(glob.glob('./images/*.png')):
    files.append(name)

# Read images with OpenCV.
images = {name: cv2.imread(name) for name in files}
w = width             # 画像の横幅を取得
h = height            # 画像の縦幅を取得

for name, image in images.items():
  # Convert the BGR image to RGB and process it with MediaPipe Pose.
  if image is None:
      break
  results = pose.process(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
  landmarks = results.pose_landmarks
  if landmarks is None:
      print('検出できなかったフレーム番号:',name)
      continue
   #各検出ポイントをarrayに変換
   #world座標系にすると左手の精度がでないので変更した
  rtshoulder=[results.pose_world_landmarks.landmark[12].x,results.pose_world_landmarks.landmark[12].y,results.pose_world_landmarks.landmark[12].z]
  rtelbow=[results.pose_world_landmarks.landmark[14].x,results.pose_world_landmarks.landmark[14].y,results.pose_world_landmarks.landmark[14].z]
  #rtwrist=[results.pose_world_landmarks.landmark[16].x,results.pose_world_landmarks.landmark[16].y,results.pose_world_landmarks.landmark[16].z]
  rthip=[results.pose_world_landmarks.landmark[24].x,results.pose_world_landmarks.landmark[24].y,results.pose_world_landmarks.landmark[24].z]
  ltshoulder=[results.pose_world_landmarks.landmark[11].x,results.pose_world_landmarks.landmark[11].y,results.pose_world_landmarks.landmark[11].z]
  ltelbow=[results.pose_world_landmarks.landmark[13].x,results.pose_world_landmarks.landmark[13].y,results.pose_world_landmarks.landmark[13].z]
  lthip=[results.pose_world_landmarks.landmark[23].x,results.pose_world_landmarks.landmark[23].y,results.pose_world_landmarks.landmark[23].z]
  nose=[results.pose_world_landmarks.landmark[0].x,results.pose_world_landmarks.landmark[0].y,results.pose_world_landmarks.landmark[0].z]
  #midshoulder=(np.array(rtshoulder)+np.array(ltshoulder))/2
  #midhip=(np.array(rthip)+np.array(lthip))/2
  #3D座標から角度を計算 2Dか3Dか選ぶ
  #rtelbowAngleは右肩-右肘-右手関節
  #rtelbowAngle=180-calculate_2D_angle(rtshoulder,rtelbow,rtwrist)
  #rtelbow_3DAngle=180-calculate_3D_angle(rtshoulder,rtelbow,rtwrist)
  #rtshoulderAngleは左肩-右肩-右肘
  rtshoulderAngle=calculate_2D_angle(ltshoulder,rtshoulder,rtelbow)
  rtshoulder_3DAngle=calculate_3D_angle(ltshoulder,rtshoulder,rtelbow)

  ltshoulderAngle=calculate_2D_angle(rtshoulder,ltshoulder,ltelbow)
  ltshoulder_3DAngle=calculate_3D_angle(rtshoulder,ltshoulder,ltelbow)  
  #rtshoulderAbductionは右股-右肩-右ひじ
  rtshoulderAbduction=calculate_2D_angle(rthip,rtshoulder,rtelbow)
  rtshoulder_3DAbduction=calculate_3D_angle(rthip,rtshoulder,rtelbow)

  ltshoulderAbduction=calculate_2D_angle(lthip,ltshoulder,ltelbow)
  ltshoulder_3DAbduction=calculate_3D_angle(lthip,ltshoulder,ltelbow)
  #肘-股関節距離/体幹長
  rtelbowhip_dist=point_distance(rtelbow,rthip,rtshoulder,rthip)
  ltelbowhip_dist=point_distance(ltelbow,lthip,ltshoulder,lthip)
  #上腕長/体幹長さの距離の計算
  rtarm_dist=point_distance(rtelbow, rtshoulder, rtshoulder,rthip)
  ltarm_dist=point_distance(ltelbow,ltshoulder,ltshoulder, lthip)

  #肩幅/体幹長
  rtshoulder_dist=point_distance(rtshoulder, ltshoulder,rtshoulder,rthip)
  ltshoulder_dist=point_distance(ltshoulder,ltelbow,ltshoulder,lthip)
  #股関節幅/体幹長
  rthip_dist=point_distance(rthip,lthip,rtshoulder,rthip)
  lthip_dist=point_distance(rthip,lthip,ltshoulder,lthip)
#リストに計算した変数を追加してゆく
  rtshoulderAnglelist.append(rtshoulderAngle)
  rtshoulderAbductionlist.append(rtshoulderAbduction)
  rtshoulder_3DAnglelist.append(rtshoulder_3DAngle)
  rtshoulder_3DAbductionlist.append(rtshoulder_3DAbduction)

  ltshoulderAnglelist.append(ltshoulderAngle)
  ltshoulderAbductionlist.append(ltshoulderAbduction)
  ltshoulder_3DAnglelist.append(ltshoulder_3DAngle)
  ltshoulder_3DAbductionlist.append(ltshoulder_3DAbduction)

  true_angle_list.append(true_angle)
  cam_angle_list.append(cam_angle)
  is_right_hand_list.append(is_right_hand)
  timelist.append(time.time())
  #肘股関節距離/体軸長
  rtelbowhip_distlist.append(rtelbowhip_dist)
  ltelbowhip_distlist.append(ltelbowhip_dist)

  #上腕長/体幹長のリスト
  rtarm_distlist.append(rtarm_dist)
  ltarm_distlist.append(ltarm_dist)

  #肩幅/体幹長のリスト
  rtshoulder_distlist.append(rtshoulder_dist)
  ltshoulder_distlist.append(ltshoulder_dist)

  #股関節幅と体幹軸の長さの比
  rthip_distlist.append(rthip_dist)
  lthip_distlist.append(lthip_dist)

  # Draw pose landmarks.
  annotated_image = image.copy()
  # Get Landmarks
  #landmarks=results.pose_landmarks.landmark
 
  """
  Holisticを使用しない場合はこの部分をコメントアウト
  
  mp_drawing.draw_landmarks(annotated_image, results.left_hand_landmarks, mp_holistic.HAND_CONNECTIONS)
  mp_drawing.draw_landmarks(annotated_image, results.right_hand_landmarks, mp_holistic.HAND_CONNECTIONS)
  mp_drawing.draw_landmarks(
      image=annotated_image, 
      landmark_list=results.face_landmarks, 
      connections=mp_holistic.FACEMESH_TESSELATION,
      landmark_drawing_spec=drawing_spec,
      connection_drawing_spec=drawing_spec)
  """
  mp_drawing.draw_landmarks(
        image=annotated_image, 
        landmark_list=results.pose_landmarks, 
        connections=mp_pose.POSE_CONNECTIONS,
        landmark_drawing_spec=drawing_spec,
        connection_drawing_spec=drawing_spec)
  
  #get coordinate poseの33か所の3次元座標データと確信度(visibilisty)をすべて結合してCSVに変換
  data_land2 = np.zeros((1,3))
    
  for x in range (0,33):#pose_landmarksかpose_world_landmarksか選ぶ
      data1 = results.pose_world_landmarks.landmark[x].x
      data2 = results.pose_world_landmarks.landmark[x].y
      data3 = results.pose_world_landmarks.landmark[x].z
      data4 = results.pose_world_landmarks.landmark[x].visibility
      keydata = np.hstack((data1,data2,data3,data4)).reshape(1,-1)
      data_land2 = np.hstack((data_land2,keydata))

  data_land2 = data_land2[:,3:]
  data_land = np.vstack((data_land,data_land2))

  final_data= np.vstack((landmarklist,data_land))
  
  cv2.imwrite(name, annotated_image)  

#savetxtではデータの型が合わないと保存でき無いことがあるのでfmtで文字の型を指定
  np.savetxt('keypoint_results.csv',final_data,delimiter = ',',fmt = '%s')


In [14]:
import pandas as pd
landmark_df = pd.read_csv('keypoint_results.csv')
display(landmark_df)

NOSE_x    NOSE_y    NOSE_z  NOSE_visibility  LEFT_EYE_INNER_x  \
0    0.038200 -0.649518 -0.249430         0.999932          0.032026   
1    0.036985 -0.649824 -0.249509         0.999934          0.031107   
2    0.043212 -0.645264 -0.229938         0.999923          0.035355   
3    0.046068 -0.648953 -0.203078         0.999910          0.037846   
4    0.031087 -0.636693 -0.231796         0.999925          0.024944   
..        ...       ...       ...              ...               ...   
133  0.040492 -0.627723 -0.303145         0.999961          0.036880   
134  0.041647 -0.625509 -0.296550         0.999938          0.036968   
135  0.036358 -0.634940 -0.291947         0.999970          0.032482   
136  0.021192 -0.613095 -0.337216         0.999957          0.018904   
137  0.034652 -0.634889 -0.258554         0.999962          0.033490   

     LEFT_EYE_INNER_y  LEFT_EYE_INNER_z  LEFT_EYE_INNER_visibility  \
0           -0.686526         -0.227415                   0.999877   
1           -0.686770         -0.227320                   0.999882   
2           -0.682404         -0.209161                   0.999853   
3           -0.686077         -0.182393                   0.999830   
4           -0.674185         -0.211512                   0.999846   
..                ...               ...                        ...   
133         -0.665374         -0.281167                   0.999923   
134         -0.663146         -0.276411                   0.999869   
135         -0.672465         -0.269069                   0.999942   
136         -0.651699         -0.316876                   0.999902   
137         -0.671909         -0.237089                   0.999921   

     LEFT_EYE_x  LEFT_EYE_y  ...  RIGHT_HEEL_z  RIGHT_HEEL_visibility  \
0      0.032402   -0.687179  ...      0.094982               0.788577   
1      0.031483   -0.687421  ...      0.094543               0.790304   
2      0.035712   -0.683030  ...      0.051680               0.793326   
3      0.038195   -0.686667  ...      0.046683               0.801175   
4      0.025289   -0.674756  ...      0.022047               0.797851   
..          ...         ...  ...           ...                    ...   
133    0.037284   -0.666071  ...      0.061573               0.822206   
134    0.037338   -0.663812  ...      0.068540               0.829530   
135    0.032875   -0.673117  ...      0.042864               0.854149   
136    0.019301   -0.652375  ...      0.026366               0.848933   
137    0.033858   -0.672563  ...      0.031586               0.819573   

     LEFT_FOOT_INDEX_x  LEFT_FOOT_INDEX_y  LEFT_FOOT_INDEX_z  \
0             0.126195           0.845582           0.135212   
1             0.125241           0.845250           0.135736   
2             0.130035           0.844758           0.132027   
3             0.131050           0.838171           0.134940   
4             0.123833           0.835542           0.117948   
..                 ...                ...                ...   
133           0.128535           0.846752           0.103735   
134           0.136088           0.842470           0.108281   
135           0.120366           0.844177           0.109647   
136           0.120246           0.841090           0.110149   
137           0.126326           0.844044           0.119892   

     LEFT_FOOT_INDEX_visibility  RIGHT_FOOT_INDEX_x  RIGHT_FOOT_INDEX_y  \
0                      0.955002           -0.017980            0.852253   
1                      0.955606           -0.017983            0.851777   
2                      0.953768           -0.000990            0.850162   
3                      0.950764            0.000656            0.846128   
4                      0.950842           -0.003649            0.844316   
..                          ...                 ...                 ...   
133                    0.958316           -0.011009            0.858862   
134                    0.961120           -0.001652    

In [15]:
#zip関数でリストをまとめてデータフレーム化
import pandas as pd
zipped=zip(true_angle_list,cam_angle_list,is_right_hand_list,
rtshoulderAnglelist,rtshoulderAbductionlist,rtshoulder_3DAnglelist,
rtshoulder_3DAbductionlist,ltshoulderAnglelist,ltshoulderAbductionlist,
ltshoulder_3DAnglelist,ltshoulder_3DAbductionlist,
rtelbowhip_distlist,ltelbowhip_distlist,
rtarm_distlist,ltarm_distlist,
rtshoulder_distlist,ltshoulder_distlist,rthip_distlist,lthip_distlist)
df = pd.DataFrame(zipped, columns = ['true_angle','cam_angle','is_right_hand',
'rtshoulderAngle','rtshoulderAbduction','rtshoulder_3DAngle',
'rtshoulder_3DAbduction','ltshoulderAngle','ltshoulderAbduction',
'ltshoulder_3DAngle','ltshoulder_3DAbduction',
'rtelbowhip_distratio','ltelbowhip_distratio',
'rtarm_distratio','ltarm_distratio',
'rtshoulder_distratio','ltshoulder_distratio','rthip_distratio','lthip_distratio'])

In [16]:
#時間列を初期化してSeriesへ
#timelistの開始数字を0に変更
np.array(timelist[0])
#d=np.full(len(timelist),timelist[0])#すべての要素がtimelistの１番目の値でlen(timelist)の行列を作成
#timelistの時間を初期化（1番目の要素を0として行列の引き算
deltatime=np.array(timelist)-np.full(len(timelist),timelist[0])
deltatime = pd.Series(deltatime)
deltatime.name='deltatime'
#deltatimeとデータフレーム(df)の結合
df= pd.concat([deltatime, df],axis=1)
#最終データの概要を確認
display(df)

deltatime  true_angle  cam_angle  is_right_hand  rtshoulderAngle  \
0     0.000000          90         30              1       150.631190   
1     0.148201          90         30              1       150.464688   
2     0.284526          90         30              1       149.394297   
3     0.423194          90         30              1       151.000291   
4     0.558870          90         30              1       152.379850   
..         ...         ...        ...            ...              ...   
133  20.148299          90         30              1       153.655121   
134  20.304236          90         30              1       155.104271   
135  20.460290          90         30              1       151.870374   
136  20.616028          90         30              1       156.286112   
137  20.770831          90         30              1       151.192489   

     rtshoulderAbduction  rtshoulder_3DAngle  rtshoulder_3DAbduction  \
0              74.080446          152.527230               79.216011   
1              73.959663          152.488008               79.164765   
2              73.443643          150.615786               77.707583   
3              75.297482          151.588203               78.466099   
4              76.839132          152.013607               79.483562   
..                   ...                 ...                     ...   
133            76.346028          154.016750               81.562686   
134            77.758670          153.885696               81.895132   
135            75.324314          152.250291               80.282425   
136            79.168823          154.064785               83.261012   
137            74.309583          150.726759               76.680214   

     ltshoulderAngle  ltshoulderAbduction  ltshoulder_3DAngle  \
0         100.397098             9.440643          105.389486   
1         100.309713             9.317912          105.309897   
2         101.276124             9.949529          106.300748   
3         102.325763            10.618787          107.099753   
4         101.790647            10.668959          106.138835   
..               ...                  ...                 ...   
133        98.342933             8.986594          103.530638   
134        99.917973            10.225187          104.990651   
135        99.272608             8.974483          104.690234   
136        97.357791             7.816079          103.314582   
137        99.718572            10.475759          103.883225   

     ltshoulder_3DAbduction  rtelbowhip_distratio  ltelbowhip_distratio  \
0                 11.128428              1.019522              0.484050   
1                 11.084880              1.019329              0.483973   
2                 12.057265              1.008102              0.470611   
3                 13.616946              1.014888              0.485529   
4                 12.385341              1.022846              0.479198   
..                      ...                   ...                   ...   
133                9.156050              1.036288              0.476873   
134               10.235467              1.038127              0.487222   
135                9.548839              1.027748              0.481217   
136                7.784332              1.045262              0.486854   
137               11.662216              0.998655              0.489028   

     rtarm_distratio  ltarm_distratio  rtshoulder_distratio  \
0           0.459931         0.537291              0.648098   
1           0.460694         0.537198              0.647703   
2           0.461089         0.556228              0.661427   
3           0.464480         0.547261              0.656706   
4           0.464523         0.548210              0.663094   
..               ...              ...                   ...   
133         0.455630         0.537717              0.656048   
134         0.453369         0.530423              0.649269   
135         0.

In [17]:
#2つのデータフレームを結合
df_final=pd.concat([df, landmark_df], axis=1)
#最終データの概要を確認
display(df_final)

deltatime  true_angle  cam_angle  is_right_hand  rtshoulderAngle  \
0     0.000000          90         30              1       150.631190   
1     0.148201          90         30              1       150.464688   
2     0.284526          90         30              1       149.394297   
3     0.423194          90         30              1       151.000291   
4     0.558870          90         30              1       152.379850   
..         ...         ...        ...            ...              ...   
133  20.148299          90         30              1       153.655121   
134  20.304236          90         30              1       155.104271   
135  20.460290          90         30              1       151.870374   
136  20.616028          90         30              1       156.286112   
137  20.770831          90         30              1       151.192489   

     rtshoulderAbduction  rtshoulder_3DAngle  rtshoulder_3DAbduction  \
0              74.080446          152.527230               79.216011   
1              73.959663          152.488008               79.164765   
2              73.443643          150.615786               77.707583   
3              75.297482          151.588203               78.466099   
4              76.839132          152.013607               79.483562   
..                   ...                 ...                     ...   
133            76.346028          154.016750               81.562686   
134            77.758670          153.885696               81.895132   
135            75.324314          152.250291               80.282425   
136            79.168823          154.064785               83.261012   
137            74.309583          150.726759               76.680214   

     ltshoulderAngle  ltshoulderAbduction  ...  RIGHT_HEEL_z  \
0         100.397098             9.440643  ...      0.094982   
1         100.309713             9.317912  ...      0.094543   
2         101.276124             9.949529  ...      0.051680   
3         102.325763            10.618787  ...      0.046683   
4         101.790647            10.668959  ...      0.022047   
..               ...                  ...  ...           ...   
133        98.342933             8.986594  ...      0.061573   
134        99.917973            10.225187  ...      0.068540   
135        99.272608             8.974483  ...      0.042864   
136        97.357791             7.816079  ...      0.026366   
137        99.718572            10.475759  ...      0.031586   

     RIGHT_HEEL_visibility  LEFT_FOOT_INDEX_x  LEFT_FOOT_INDEX_y  \
0                 0.788577           0.126195           0.845582   
1                 0.790304           0.125241           0.845250   
2                 0.793326           0.130035           0.844758   
3                 0.801175           0.131050           0.838171   
4                 0.797851           0.123833           0.835542   
..                     ...                ...                ...   
133               0.822206           0.128535           0.846752   
134               0.829530           0.136088           0.842470   
135               0.854149           0.120366           0.844177   
136               0.848933           0.120246           0.841090   
137               0.819573           0.126326           0.844044   

     LEFT_FOOT_INDEX_z  LEFT_FOOT_INDEX_visibility  RIGHT_FOOT_INDEX_x  \
0             0.135212                    0.955002           -0.017980   
1             0.135736                    0.955606           -0.017983   
2             0.132027                    0.953768           -0.000990   
3             0.134940                    0.950764            0.000656   
4             0.117948                    0.950842           -0.003649   
..                 ...                         ...                 ...   
133           0.103735                    0.958316           -0.011009   
134           0.108281                    0.961120           -0.001652   
135        

In [18]:
#CSVに保存
df_final.to_csv(movie_name+'.csv',index=False)

# 処理した画像をmp4動画に変換


In [19]:
# 既に output.mp4 があれば削除
import os
if os.path.exists('./output.mp4'):
   os.remove('./output.mp4')

! ffmpeg -r 10 -i images/%6d.png\
               -vcodec libx264 -pix_fmt yuv420p output.mp4

ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-li

In [20]:
# --- mp4動画の再生 ---
from IPython.display import HTML
from base64 import b64encode

mp4 = open('./output.mp4', 'rb').read()
data_url = 'data:video/mp4;base64,' + b64encode(mp4).decode()
HTML(f"""
<video width="85%" height="85%" controls>
      <source src="{data_url}" type="video/mp4">
</video>""")

＊作成したmp4動画は、左側のファイル欄にある　./mediapipe/output.mp4 を右クリックするとダウンロードできます。